In [1]:
# Transformers installation
! pip install -U accelerate
! pip install -U transformers
# To install from source instead of the last release, comment the command above and uncomment the following one.
# ! pip install git+https://github.com/huggingface/transformers.git

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.6/302.6 kB 7.3 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl (196.0 MB)
  Using cached nvidia_nccl_cu12-2.19.3-py3-none-manylinux1_x86_64.whl (166.0 MB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-many

In [2]:
!pip install datasets evaluate

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 542.0/542.0 kB 8.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.1/84.1 kB 11.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 10.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 401.2/401.2 kB 13.9 MB/s eta 0:00:00
  Attempting uninstall: huggingface-hub
    Found existing installation: huggingface-hub 0.20.3
    Uninstalling huggingface-hub-0.20.3:
      Successfully uninstalled huggingface-hub-0.20.3


## Carga del dataset

Login en HuggingFace

In [3]:
from huggingface_hub import notebook_login

notebook_login()

Carga del dataset 'climate_change'

In [16]:
from datasets import load_dataset

climate_train = load_dataset("somosnlp/spa_climate_detection", split="train")
climate_test = load_dataset("somosnlp/spa_climate_detection", split="test")

climate_train = climate_train.class_encode_column('answer')
climate_test = climate_test.class_encode_column('answer')

climate_train = climate_train.select_columns(['question', 'answer'])
climate_test = climate_test.select_columns(['question', 'answer'])

climate_train = climate_train.rename_columns({'question': 'text', 'answer': 'label'})
climate_test = climate_test.rename_columns({'question': 'text', 'answer': 'label'})

climate_train.features
#climate_test[0]

{'text': Value(dtype='string', id=None),
 'label': ClassLabel(names=['0', '1'], id=None)}

## Preprocessing

In [19]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("bertin-project/bertin-roberta-base-spanish")

Funcion de preprocessing

In [21]:
def preprocess_function(examples):
    return tokenizer(examples["text"], truncation=True)

tokenized_climate_train = climate_train.map(preprocess_function, batched=True)
tokenized_climate_test = climate_test.map(preprocess_function, batched=True)

Map:   0%|          | 0/2900 [00:00<?, ? examples/s]

Map:   0%|          | 0/780 [00:00<?, ? examples/s]

Batch of examples

In [22]:
from transformers import DataCollatorWithPadding

data_collator = DataCollatorWithPadding(tokenizer=tokenizer)

## Evaluate

In [23]:
import evaluate

accuracy = evaluate.load("accuracy")

Funcion de evaluacion

In [24]:
import numpy as np


def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    predictions = np.argmax(predictions, axis=1)
    return accuracy.compute(predictions=predictions, references=labels)

## Train

Ids to labels

In [25]:
id2label = {0: "NEGATIVE", 1: "POSITIVE"}
label2id = {"NEGATIVE": 0, "POSITIVE": 1}

Cargando el modelo

In [26]:
from transformers import AutoModelForSequenceClassification, TrainingArguments, Trainer

model = AutoModelForSequenceClassification.from_pretrained(
    "bertin-project/bertin-roberta-base-spanish", num_labels=2, id2label=id2label, label2id=label2id
)

Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at bertin-project/bertin-roberta-base-spanish and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [12]:
#!pip install transformers[torch]
!python -m pip install accelerate -U
#!python -m pip install git+https://github.com/huggingface/accelerate

In [13]:
!accelerate config

----------------------------------------------------------------------------------------------------In which compute environment are you running?
Please input a choice index (starting from 0), and press enter
 ➔  This machine
    AWS (Amazon SageMaker)
0
This machine
----------------------------------------------------------------------------------------------------Which type of machine are you using?
Please input a choice index (starting from 0), and press enter
 ➔  No distributed training
    multi-CPU
    multi-XPU
    multi-GPU
    multi-NPU
    multi-MLU
    TPU
0
No distributed training
Do you want to run your training on CPU only (even if a GPU / Apple Silicon / Ascend NPU device is available)? [yes/NO]:NO
Do you wish to optimize your script with torch dynamo?[yes/NO]:NO
Do you want to use DeepSpeed? [yes/NO]: NO
What GPU(s) (by id) should be used for training on this machine as a comma-seperated list? [all]:all
Would you like to enable numa efficiency? (Currently only supported

In [27]:
import accelerate

accelerate.__version__

'0.30.1'

In [28]:
training_args = TrainingArguments(
    output_dir="bertin_base_climate_detection_spa_v2",
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=2,
    weight_decay=0.01,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_climate_train,
    eval_dataset=tokenized_climate_test,
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
)

trainer.train()

TrainOutput(global_step=364, training_loss=0.2180901621724223, metrics={'train_runtime': 506.3435, 'train_samples_per_second': 11.455, 'train_steps_per_second': 0.719, 'total_flos': 1432162807647360.0, 'train_loss': 0.2180901621724223, 'epoch': 2.0})

In [29]:
trainer.push_to_hub("Gerard-1705/bertin_base_climate_detection_spa_v3")

events.out.tfevents.1715443744.cabd175de39c.462.0:   0%|          | 0.00/4.92k [00:00<?, ?B/s]

Upload 4 LFS files:   0%|          | 0/4 [00:00<?, ?it/s]

model.safetensors:   0%|          | 0.00/499M [00:00<?, ?B/s]

training_args.bin:   0%|          | 0.00/5.05k [00:00<?, ?B/s]

events.out.tfevents.1715444119.cabd175de39c.462.1:   0%|          | 0.00/5.92k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/Gerard-1705/bertin_base_climate_detection_spa_v2/commit/b5c6e4efc59fe94636da088a21f572f279ca897d', commit_message='Gerard-1705/bertin_base_climate_detection_spa_v3', commit_description='', oid='b5c6e4efc59fe94636da088a21f572f279ca897d', pr_url=None, pr_revision=None, pr_num=None)

## INFERENCE

In [37]:
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("somosnlp/bertin_base_climate_detection_spa")
tokenizer.model_max_length
from transformers import AutoModelForSequenceClassification
import torch

model = AutoModelForSequenceClassification.from_pretrained("somosnlp/bertin_base_climate_detection_spa")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/1.23k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/851k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/509k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.21M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/957 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/920 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/499M [00:00<?, ?B/s]

In [38]:
tokenizer.model_max_length
tokenizer.model_max_length = 512

Validamos el modelo con un set de 200 rows

In [39]:
text = "El bioma dominante en Zambia es la sabana. Gran parte del centro, norte y oeste del país está ocupado por la ecorregión denominada sabana arbolada de miombo del Zambeze central. Al sureste se alternan la sabana arbolada de miombo meridional y la sabana arbolada de mopane del Zambeze."
inputs = tokenizer(text, return_tensors="pt")

In [40]:
with torch.no_grad():
    logits = model(**inputs).logits
predicted_class_id = logits.argmax().item()
model.config.id2label[predicted_class_id]

'NEGATIVE'

In [41]:
import pandas as pd
val_df = pd.read_csv("validation_dataset.csv", delimiter=';', on_bad_lines='warn')
print(val_df.shape)

(200, 1)


In [42]:
val_inputs = []
val_outputs = []
for txt in val_df['text']:
  print(txt)
  inputs = tokenizer(txt, return_tensors="pt", truncation=True)
  with torch.no_grad():
    logits = model(**inputs).logits
  predicted_class_id = logits.argmax().item()
  val_outputs.append(predicted_class_id)
  print(model.config.id2label[predicted_class_id])

El consumo de energía residencial aumenta rápidamente cada año debido a cambios demográficos y de comportamiento, como el aumento de la población y la adopción del trabajo desde casa tras el COVID-19. El elevado consumo de energía emite una cantidad sustancial de dióxido de carbono y otros gases de efecto invernadero, lo que contribuye al calentamiento global. Resulta crucial predecir con exactitud la carga residencial. Para permitir un control inteligente del consumo eléctrico doméstico, así como una generación, planificación y uso eficientes, predecimos el consumo energético doméstico a muy corto plazo, a corto plazo y a medio plazo utilizando datos de series temporales univariantes y multivariantes. Este estudio evalúa el impacto de diferentes unidades domésticas (calentador de agua y aire acondicionado), zonas (cocina, lavandería, despacho, salón, baño, cuarto de plancha, habitación de los adolescentes y habitación de los padres) y tiempo (es decir, hora, día y mes) en el consumo d

In [43]:
temp_eval = dict(output = val_outputs)
out_df = pd.DataFrame(temp_eval)
out_df.to_csv('out_eval.csv', sep=';', index=False)